# ICME_SOLO_MOESTL_20220622_01

This notebook documents the off-web workflow to use 3DCORE.

## Data Preprocessing

In [2]:
# import packages
from coreweb.methods.offwebutils import get_modelkwargs_ranges, offwebfit, get_eventinfo, update_posfig_offweb
from coreweb.dashcore.utils.plotting import check_animation, check_fittingpoints
from coreweb.dashcore.utils.utils import load_fit
from coreweb.dashcore.assets.config_sliders import modelslidervars, magslidervars
from coreweb.dashcore.app import update_launch_label, generate_graphstore
from coreweb.dashcore.pages.Start import update_alert_for_init

import pandas as pd
from IPython.display import display, HTML

import datetime

import warnings
warnings.filterwarnings('ignore')

In [3]:
# import and process data

reference_frame = "RTN" # switch to HEEQ if needed 
idd = 'ICME_SOLO_MOESTL_20220622_01'

eventinfo = get_eventinfo(idd)
graphstore, posstore, _ = generate_graphstore(eventinfo, reference_frame, {})


{'processday': ['2022-06-22T03:31:00'], 'begin': ['2022-06-22T03:31:00'], 'end': ['2022-06-22T17:41:00'], 'sc': ['SolarOrbiter'], 'id': ['ICME_SOLO_MOESTL_20220622_01'], 'loaded': False, 'changed': True}
Data loaded from /Users/hannahruedisser/3DCOREweb/src/coreweb/dashcore/data/ICME_SOLO_MOESTL_20220622_01.pkl


## Plots

Plotting insitu data and positions can be helpful to analyse a given event. Adapting the model and magnetic field parameters influences both 3D shape and insitu magnetic field, as seen in the plots below.

### Set parameters for the model

In [7]:
# launchtime, set hours to impact
deltalaunch = -88.5
launchlabel, _ = update_launch_label(eventinfo, deltalaunch)

print(launchlabel)
print('Insitu Start of Event: ' + datetime.datetime.strptime(eventinfo['begin'][0], "%Y-%m-%dT%H:%M:%S").strftime("%Y-%m-%d %H:%M"))


# model parameters

# Longitude (HEEQ)     [deg.]      
# -180.00 to 360.00
longit = 0. 

# Latitude (HEEQ)     [deg.]      
# -90.00 to 90.00
latitu = 0. 

# Inclination     [deg.]      
# 0.00 to 360.00
inc = 0. 

# Diameter 1 AU     [AU]      
# 0.05 to 0.35
dia = 0.2

# Aspect Ratio     []      
# 1.0 to 6.0
asp = 3.

# Launch Radius     [R_Sun]      
# 5. to 100.
l_rad = 20.

# Launch Velocity     [km/s]      
# 400. to 3000.
l_vel = 800.

# Expansion Rate     []      
# 0.30 to 2.00
exp_rat = 1.14

# Background Drag     []      
# 0.20 to 3.00
b_drag = 1.00

# Background Velocity     [km/s]      
# 100. to 700.
bg_vel = 500.


# magnetic field parameters

# T_Factor     []      
# -250. to 250.
t_fac = 100.

# Magnetic Decay Rate     []      
# 1.00 to 2.00
mag_dec = 1.64

# Magnetic Field Strength 1 AU     [nT]      
# 5. to 150.
mag_strength = 25.


Launch Time: 2022-06-18 11:00
Insitu Start of Event: 2022-06-22 03:31


### Show a simple position overview

In [8]:
# plot positions


# choose from the following plot options: "Title", "Latitudinal Grid", "Longitudinal Grid","Trajectories","Synthetic Event","Catalog Event","AU axis","Trajectories","Parker Spiral","Catalog Event", "Timer"
plot_options = [
    "Title", 
    "Longitudinal Grid",
    "Trajectories",
    "Synthetic Event",
    "Catalog Event",
    "AU axis",
    "Trajectories",
    "Parker Spiral",
    "Catalog Event", 
    "Timer"]

# choose from the following spacecraft: "SOLO", "PSP", "BEPI", "Wind","STEREO-A", "SYN"
spacecraftoptions =["SOLO", "PSP", "BEPI", "STEREO-A"]

# choose from the following bodies: "Sun", "Mercury", "Venus","Earth"
bodyoptions = ["Sun", "Mercury", "Venus","Earth"]

modelstatevars = [longit, latitu, inc, dia, asp, l_rad, l_vel, exp_rat, b_drag, bg_vel, t_fac, mag_dec, mag_strength]

togglerange = 0 # set to 0/1 to switch the longitude range
dim = "3D" # set to 2D/3D
currenttimeslider = 25 # set time since launch, irrelevant for 2D plot

# this function produces the figure
update_posfig_offweb(posstore, None, None, None,  togglerange, currenttimeslider, dim, graphstore, eventinfo, launchlabel, plot_options, spacecraftoptions, bodyoptions, reference_frame, *modelstatevars)[0]

### Show insitu data and 3D Plot

In [9]:
# choose from the following plot options: "Title", "Latitudinal Grid", "Longitudinal Grid","Trajectories","Synthetic Event","Catalog Event","AU axis","Trajectories","Parker Spiral","Catalog Event", "Timer"
plot_options = [
    "Title", 
    "Longitudinal Grid",
    "Trajectories",
    "Synthetic Event",
    "Catalog Event",
    "AU axis",
    "Trajectories",
    "Parker Spiral",
    "Catalog Event", 
    "Timer"]

# choose from the following spacecraft: "SOLO", "PSP", "BEPI", "Wind","STEREO-A", "SYN"
spacecraftoptions =["SOLO", "PSP", "BEPI", "STEREO-A"]

# choose from the following bodies: "Sun", "Mercury", "Venus","Earth"
bodyoptions = ["Sun", "Earth"]

#modelstatevars = [longit, latitu, inc, dia, asp, l_rad, l_vel, exp_rat, b_drag, bg_vel, t_fac, mag_dec, mag_strength]

view_legend_insitu = True
insitu = True
positions = True
plottheme = 'light-simple' # 'dark', 'light', 'dark-simple', 'light-simple'

camera = [1.0,-15,0] #'auto' give r, lon and lat

# this function creates the figure
checkanim = check_animation(plottheme, graphstore, reference_frame, None, None, None, currenttimeslider, eventinfo, launchlabel, plot_options, spacecraftoptions, bodyoptions,  insitu, positions, view_legend_insitu, camera, posstore, *modelstatevars)
#checkanim.write_html("checkanim.html")
checkanim

## Fitting

We use an ABC Monte Carlo algorithm to fit the model to insitu data.

### Set the fitting points

These are used to determine the limits of an event and datapoints to calculate the RMSE during fitting. If these are not set, they will be automatically determined.

In [10]:
t_launch = datetime.datetime(2022, 6, 18, 11, tzinfo=datetime.timezone.utc) # choose launch time

t_s = datetime.datetime(2022, 6, 22, 3,30, tzinfo=datetime.timezone.utc) # use start time of event
t_e = datetime.datetime(2022, 6, 22, 18, 00, tzinfo=datetime.timezone.utc) # use end time of event

# choose arbitrary number of fitting points within the event

t_fit = [
    datetime.datetime(2022, 6, 22, 6, tzinfo=datetime.timezone.utc),
    datetime.datetime(2022, 6, 22, 8, 30, tzinfo=datetime.timezone.utc),
    datetime.datetime(2022, 6, 22, 11, tzinfo=datetime.timezone.utc),
    datetime.datetime(2022, 6, 22, 13,30, tzinfo=datetime.timezone.utc),
    datetime.datetime(2022, 6, 22, 16, tzinfo=datetime.timezone.utc),
 ]

showtitle = True

# this function creates a figure to visually check the previously set points
fig, t_s, t_e, t_fit = check_fittingpoints(graphstore, reference_frame, eventinfo, view_legend_insitu, showtitle, t_fit, t_s, t_e) 
fig

### Set the parameter ranges and fitting parameters

In [11]:
ensemblesize = int(2**16)

# model parameters

# Longitude (HEEQ)     [deg.]      
# -180.00 to 360.00
longit_range = [160.,180.] 

# Latitude (HEEQ)     [deg.]      
# -90.00 to 90.00
latitu_range = [-45.,45.] 

# Inclination     [deg.]      
# 0.00 to 360.00
inc_range = [0.,360.] 

# Diameter 1 AU     [AU]      
# 0.05 to 0.35
dia_range = [0.05,0.35]

# Aspect Ratio     []      
# 1.0 to 6.0
asp_range = [1.,6.]

# Launch Radius     [R_Sun]      
# 5. to 100.
l_rad_range = [10.,20.]

# Launch Velocity     [km/s]      
# 400. to 3000.
l_vel_range = [400.,3000.]

# Expansion Rate     []      
# 0.30 to 2.00
exp_rat_range = [1.14,1.14]

# Background Drag     []      
# 0.20 to 3.00
b_drag_range = [0.20,3.00]

# Background Velocity     [km/s]      
# 100. to 700.
bg_vel_range = [100.,700.]


# magnetic field parameters

# T_Factor     []      
# -250. to 250.
t_fac_range = [-250.,250.]

# Magnetic Decay Rate     []      
# 1.00 to 2.00
mag_dec_range = [1.64,1.64]

# Magnetic Field Strength 1 AU     [nT]      
# 5. to 150.
mag_strength_range = [5.,20.]

multiprocessing = True

njobs = 4

itermin = 13
itermax = 15

n_particles = 512

### Start the fitting process

In [10]:
# preprocess the set arguments
modelstatevar_ranges = [ensemblesize] + [longit_range, latitu_range, inc_range, dia_range, asp_range, l_rad_range, l_vel_range, exp_rat_range, b_drag_range, bg_vel_range, t_fac_range, mag_dec_range, mag_strength_range]
modelkwargs = get_modelkwargs_ranges(modelstatevar_ranges)

# start the fitting process
filepath = offwebfit(t_launch, eventinfo, graphstore, multiprocessing, t_s, t_e, t_fit, njobs, itermin, itermax, n_particles, modelkwargs)

Running iteration 0
Initial eps_init =  [1.2079366]
Starting simulations
Multiprocessing is used
529 reached particles                     
Setting new eps: [1.18377787] => [0.93089062]
Step 0 done, 8.65M runs in 74.60 seconds, (total: 00h 01m 14s)
Created directory /Users/hannahruedisser/3DCOREweb/src/coreweb/dashcore/output/ICME_SOLO_MOESTL_20220622_01_HEEQ_202311141706/00.pickle
Saved to /Users/hannahruedisser/3DCOREweb/src/coreweb/dashcore/output/ICME_SOLO_MOESTL_20220622_01_HEEQ_202311141706/00.pickle
Running iteration 1
Starting simulations
Multiprocessing is used
531 reached particles                     
Setting new eps: [0.93089062] => [0.79735512]
Step 1 done, 2.10M runs in 31.63 seconds, (total: 00h 01m 46s)
Saved to /Users/hannahruedisser/3DCOREweb/src/coreweb/dashcore/output/ICME_SOLO_MOESTL_20220622_01_HEEQ_202311141706/01.pickle
Running iteration 2
Starting simulations
Multiprocessing is used
515 reached particles                     
Setting new eps: [0.79735512] => [0.

In [12]:
filepath = '/Users/hannahruedisser/3DCOREweb/src/coreweb/dashcore/output/ICME_SOLO_MOESTL_20220622_01_HEEQ_202311141706/05.pickle' 

## Result Analysis

### Show the fitting results

The fitting results can be shown as a scatterplot or in a table.

In [13]:
tablenew, *fitting_values, resdfdic, t0, mean_row, statfig = load_fit(filepath.split('/')[-2], graphstore)

statfig

In [15]:
df = pd.DataFrame.from_dict(resdfdic)

pd.set_option("display.max_rows", None)

# Puts the scrollbar next to the DataFrame
display(HTML("<div style='height: 200px; overflow: auto; width: fit-content'>" +
             df.style.render() +
             "</div>"))

In [ ]:
restable

## Movie Creation

Create a simulation movie

### set movie parameters